# LAB 06 Assigment

Dominik Breksa (dominikbreksa@student.agh.edu.pl)

In [18]:
"""LAB 06 Assigment Solution Notebook"""

from functools import partial

import matplotlib.pyplot as plt
import numpy as np
import scipy
from open_atmos_jupyter_utils import show_plot

### Goal

The goal of the analysis is to implement and experiment with the two-dimensional monte carlo solver which will model advection of, for example, mass as a particle movement.



In [19]:
DTYPE = np.float64

In [20]:
NX = 45
X, DX = np.linspace(0., 12., num=NX, dtype=DTYPE, retstep=True, endpoint=True)
NY = 30
Y, DY = np.linspace(0., 6., num=NY, dtype=DTYPE, retstep=True, endpoint=True)
NT = 45
T, DT = np.linspace(0., 5., num=NT, dtype=DTYPE, retstep=True, endpoint=True)

In [21]:
X_SPEED, Y_SPEED = 1, 0.5

In [22]:
N_PART, N_REAL = 2_500, 2_500_000

In [23]:
X_0, Y_0 = 2., 2.
SIGMA_X, SIGMA_Y = 0.5, 0.5

In [24]:
X_SCIPY_RNG = scipy.stats.norm(loc=X_0, scale=SIGMA_X)
Y_SCIPY_RNG = scipy.stats.norm(loc=Y_0, scale=SIGMA_Y)
XY_SCIPY_RNG = scipy.stats.multivariate_normal(mean=(X_0, Y_0), cov=[[SIGMA_X, 0.],
                                                                     [0., SIGMA_Y]])
NP_RNG = np.random.default_rng(seed=44)

In [25]:
def sample():
    """ sample function modified to suit 2d environment """
    u01_x = NP_RNG.uniform(0., 1., N_PART)
    u01_y = NP_RNG.uniform(0., 1., N_PART)
    span_x = X.max() - X.min()
    span_y = Y.max() - Y.min()
    return {
        k: {
            'cell_x': (v['cell_x'] / DX).astype(int),
            'cell_y': (v['cell_y'] / DY).astype(int),
            'mult': np.round(v['mult'] * N_REAL).astype(int),
        }
        for k,v in {
            'uniform in space': {
                'cell_x': u01_x * span_x,
                'cell_y': u01_y * span_y,
                'mult': (
                    XY_SCIPY_RNG.pdf(np.dstack((u01_x * span_x, u01_y * span_y)))
                    * span_x
                    * span_y
                    / N_PART
                ),
            },
            'constant multiplicity': {
                'cell_x': X_SCIPY_RNG.ppf(u01_x),
                'cell_y': Y_SCIPY_RNG.ppf(u01_y),
                'mult': np.ones(shape=(N_PART,), dtype=DTYPE) / N_PART,
            },
        }.items()
    }

PARTICLES = sample()

Illustration of the initial conditions of spacial displacement of particles for both sampling methods.

In [26]:
def plot(*, particles, t, disp = 0.2):
    """ plots the current displacement of particles at any given time """
    fig, axs = plt.subplot_mosaic([['h_x', '.'], ['scat', 'h_y']],
                                  figsize=(9, 6),
                                  width_ratios=(4, 1), height_ratios=(1, 4),
                                  layout='constrained')
    span_x = X.max() - X.min()
    span_y = Y.max() - Y.min()
    u01_x = NP_RNG.uniform(-disp, disp, N_PART)
    u01_y = NP_RNG.uniform(-disp, disp, N_PART)

    for k in particles:
        axs['h_x'].hist(
            x=particles[k]['cell_x'],
            weights=particles[k]['mult'] / N_REAL,
            bins=NX, range=(0, NX), alpha=.666,
        )
        axs['h_y'].hist(
            x=particles[k]['cell_y'],
            weights=particles[k]['mult'] / N_REAL,
            bins=NY, range=(0, NY), alpha=.666, orientation='horizontal',
        )
        axs['scat'].scatter(
            x=((particles[k]['cell_x'] * DX) + u01_x + disp) / (span_x + disp) * span_x,
            y=((particles[k]['cell_y'] * DY) + u01_y + disp) / (span_y + disp) * span_y,
            s=.25 + particles[k]['mult'] * N_PART / N_REAL / 2, label=f'{k}',
        )

    axs['h_x'].set_ylabel('pdf(x) ⋅ Δx [1]')
    axs['h_x'].plot(X / DX, X_SCIPY_RNG.pdf(X - X_SPEED * t) * DX, '-k', label='analytic')
    axs['h_x'].set_xlim(0, NX)
    axs['h_x'].set_xticks(range(0, NX + 1, 2))
    axs['h_x'].grid()
    axs['h_y'].set_xlabel('pdf(y) ⋅ Δy [1]')
    axs['h_y'].plot(Y_SCIPY_RNG.pdf(Y - Y_SPEED * t) * DY, Y / DY, '-k')
    axs['h_y'].set_ylim(0, NY)
    axs['h_y'].set_yticks(range(0, NY + 1, 2))
    axs['h_y'].grid()

    axs['scat'].set_xlabel('x [m]')
    axs['scat'].set_ylabel('y [m]')
    axs['scat'].set_xlim(X.min(), X.max())
    axs['scat'].set_ylim(Y.min(), Y.max())
    scat_2x = axs['scat'].twinx()
    scat_2y = axs['scat'].twiny()
    scat_2x.set_ylabel('y / Δy [1]')
    scat_2x.set_ylim(0, NY)
    scat_2x.set_yticks(range(0, NY + 1, 2))
    scat_2x.grid()
    scat_2y.set_xlabel('x / Δx [1]')
    scat_2y.set_xlim(0, NX)
    scat_2y.set_xticks(range(0, NX + 1, 2))
    scat_2y.grid()

    fig.suptitle(f'Concentration of particles at time={t} [s]', fontsize=12)
    fig.legend(loc='upper right', markerscale=2.0)
    show_plot(fig=fig)

plot(particles=PARTICLES, t=0)

### Analytical solution for 2d advection equation

Since the only two requirements on the flow field are that it needs to be constant in time and must have both components above zero, the simplest flow-field meeting these criteria is a constant in time and space flow-field.

This flow-field can be simplified to solving $N=2$ dimensional homogeneous transport differential equation listed below:

$$
\frac{\partial c(x, y, t)}{\partial t} + u \frac{\partial c(x, y, t)}{\partial x} + v \frac{\partial c(x, y, t)}{\partial y} = 0 \qquad (u \ne 0; v \ne 0)
$$

The solution to this equation is:

$$
c(x, y, t) = c(x - ut, y - vt, 0) \qquad (t \ge 0)
$$

Python implementation:

In [27]:
def initial_conditions(x, y):
    """ https://en.wikipedia.org/wiki/Multivariate_normal_distribution """
    return XY_SCIPY_RNG.pdf(np.dstack((x, y)))

In [28]:
def analytical_solution(x, y, t, x_speed, y_speed):
    """ function implementing the analytical solution of the problem """
    return initial_conditions(x - x_speed * t, y - y_speed * t)

In [29]:
ANALYTICAL_SOL = partial(analytical_solution, x_speed=X_SPEED, y_speed=Y_SPEED)

### Numerical solution for 2d advection equation using monte carlo sampling

In my case, the flow field is constant in time and space. However, the goal of the assignment was to generalise the advection solver so that it can work with any constant in time flow field, so I went an extra mile to make it happen.

My flow field is implemented as a courant number (probability) array of the size corresponding to the grid size. I will take the probability value at a place in space where the particle is and then make a coin flip if the particle should move to the next grid bin in a given unit direction.

In [30]:
def flow_field(nx, dx, ny, dy, dt):
    """ creates a flow field for every cell """
    assert 0. < abs(x_courant_num := X_SPEED * dt / dx) <= 1.
    assert 0. < abs(y_courant_num := Y_SPEED * dt / dy) <= 1.

    flow_field_data = (
        np.full((nx, ny, 1), x_courant_num, dtype=DTYPE),
        np.full((nx, ny, 1), y_courant_num, dtype=DTYPE),
    )

    return np.concat(flow_field_data, axis=-1, dtype=DTYPE)

FLOW_FIELD = flow_field(NX, DX, NY, DY, DT)

In [31]:
def advect(*, particles, flow_field_data):
    """ performs Monte-Carlo advection of particles """
    for _ in range(NT):
        u01_x = NP_RNG.uniform(0., 1., N_PART)
        u01_y = NP_RNG.uniform(0., 1., N_PART)
        for part in particles.values():
            flow_values = flow_field_data[np.where(part['cell_x'] < NX, part['cell_x'], NX - 1),
                                          np.where(part['cell_y'] < NY, part['cell_y'], NY - 1)]
            c_x = flow_values[:, 0]
            c_y = flow_values[:, 1]
            part['cell_x'] += (abs(c_x) > u01_x) * (np.abs(c_x) / c_x).astype(int)
            part['cell_y'] += (abs(c_y) > u01_y) * (np.abs(c_y) / c_y).astype(int)

advect(particles=PARTICLES, flow_field_data=FLOW_FIELD)

Results of particle movement after T.max() seconds from initial conditions.

In [32]:
plot(particles=PARTICLES, t=T.max())

### Analysis of the results

The metric for computing the error is the Root Mean Square Error (RMSE).

In [33]:
def root_mean_square_error(x_pred, x_true):
    """ computes RMSE """
    assert x_pred.shape == x_true.shape
    return np.sqrt(np.mean((x_pred - x_true) ** 2))

In [34]:


# ERROR = root_mean_square_error(1, ANALYTICAL_SOL(X, Y, T.max()) * DX * DY)

In [35]:
def plot_error():
    """ plots the error """

Conclusions:

- After the advection we can observe that the particles moved predictably to their velocity along axes multiplied by the passed time.
- On the plots we can see that compared to the analytical solution, the monte carlo method undergoes some dispersion similarly to numerical diffusion in the finite difference methods. However, the peaks in the histograms still follow the peaks of predicted analytical solutions.
- ...